1. Make a master file containing all features of all persons
2. Calculate one more temporal feature and a location-based feature 'time_diff_in_minute' and 'geo_dist, and them to the master file

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import math
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error


In [2]:
#read the intermediate file created in step D3
path ='emotional_rating_18P_allF_minutes.csv' # use your path

#File_ = glob.glob(path1 + "/*.csv")


df= pd.read_csv(path)
df.head()

timestamp  ACTIVE  AFRAID  ALERT  AMUSED  ANGRY  ASHAMED  ATTENTIVE  \
0  1.440094e+09     0.0     0.0    0.0     0.0    0.0      0.0        0.0   
1  1.440094e+09     0.0     0.0    0.0     0.0    0.0      0.0        0.0   
2  1.440094e+09     0.0     0.0    0.0     0.0    0.0      0.0        0.0   
3  1.440094e+09     0.0     0.0    0.0     0.0    0.0      0.0        0.0   
4  1.440094e+09     0.0     0.0    0.0     0.0    0.0      0.0        0.0   

   BORED  CALM  ...  day_of_timestamp  day_of_month  cl_latitude  \
0    0.0   0.0  ...                 3            20       32.881   
1    0.0   0.0  ...                 3            20       32.881   
2    0.0   0.0  ...                 3            20       32.881   
3    0.0   0.0  ...                 3            20       32.880   
4    0.0   0.0  ...                 3            20       32.880   

   cl_longitude  minute_of_hour  minute_of_day  pleasant_score  arousal_score  \
0      -117.234               7           1087            8.47           6.05   
1      -117.234               8           1088            8.47           6.05   
2      -117.235               9           1089            8.47           6.05   
3      -117.235              10           1090            8.47           6.05   
4      -117.235              11           1091            8.47           6.05   

   dominance_score  emotion  
0             7.21      2.0  
1             7.21      2.0  
2             7.21      2.0  
3             7.21      2.0  
4             7.21      2.0  

[5 rows x 341 columns]

In [3]:
p_list=df['person'].unique()
p_list

array([ 8, 10, 12, 13, 15, 20, 21, 25, 27, 33, 35, 40, 46, 48, 49, 52, 54,
       55], dtype=int64)

In [4]:
#drop 49 discrete emotion labels and binary temporal features

sel_feat_df=df.drop(['ACTIVE','AFRAID','ALERT','AMUSED','ANGRY','ASHAMED','ATTENTIVE','BORED',\
                      'CALM','CRAZY','DETERMINED','DISGUSTED','DISTRESSED','DREAMY','ENERGETIC','ENTHUSIASTIC',\
                      'EXCITED','FRUSTRATED','GUILTY','HAPPY','HIGH','HOSTILE','HUNGRY','IN_EMOTIONAL_PAIN','IN_LOVE','IN_PHYSICAL_PAIN','INSPIRED',\
                      'INTERESTED','IRRITABLE','JITTERY','LONELY','NERVOUS','NORMAL','NOSTALGIC','OPTIMISTIC','PHYSICALLY_SICK',\
                      'PROUD','ROMANTIC','SAD','SCARED','SERIOUS','SEXY','SLEEPY','STRESSED','STRONG','TIRED','UNTROUBLED','UPSET','WORRIED',\
                     'discrete:time_of_day:between0and6','discrete:time_of_day:between3and9','discrete:time_of_day:between6and12','discrete:time_of_day:between9and15',\
                     'discrete:time_of_day:between12and18','discrete:time_of_day:between15and21','discrete:time_of_day:between18and24','discrete:time_of_day:between21and3',], axis=1)
#print the list of the features
list(sel_feat_df)

['timestamp',
 'person',
 'raw_acc:magnitude_stats:mean',
 'raw_acc:magnitude_stats:std',
 'raw_acc:magnitude_stats:moment3',
 'raw_acc:magnitude_stats:moment4',
 'raw_acc:magnitude_stats:percentile25',
 'raw_acc:magnitude_stats:percentile50',
 'raw_acc:magnitude_stats:percentile75',
 'raw_acc:magnitude_stats:value_entropy',
 'raw_acc:magnitude_stats:time_entropy',
 'raw_acc:magnitude_spectrum:log_energy_band0',
 'raw_acc:magnitude_spectrum:log_energy_band1',
 'raw_acc:magnitude_spectrum:log_energy_band2',
 'raw_acc:magnitude_spectrum:log_energy_band3',
 'raw_acc:magnitude_spectrum:log_energy_band4',
 'raw_acc:magnitude_spectrum:spectral_entropy',
 'raw_acc:magnitude_autocorrelation:period',
 'raw_acc:magnitude_autocorrelation:normalized_ac',
 'raw_acc:3d:mean_x',
 'raw_acc:3d:mean_y',
 'raw_acc:3d:mean_z',
 'raw_acc:3d:std_x',
 'raw_acc:3d:std_y',
 'raw_acc:3d:std_z',
 'raw_acc:3d:ro_xy',
 'raw_acc:3d:ro_xz',
 'raw_acc:3d:ro_yz',
 'proc_gyro:magnitude_stats:mean',
 'proc_gyro:magnitud

In [5]:
# calculate time difference between two consecutive rows
d_df=pd.DataFrame()
d_df['timestamp']=pd.to_datetime(sel_feat_df['timestamp'], unit='s')
new_col=d_df['timestamp'].diff()/np.timedelta64(1,'m')
new_col.iloc[0]=0
sel_feat_df.insert(loc=sel_feat_df.shape[1]-4, column='time_diff_in_minute', value=new_col)
sel_feat_df.head()

timestamp  person  raw_acc:magnitude_stats:mean  \
0  1.440094e+09       8                      1.001473   
1  1.440094e+09       8                      1.020985   
2  1.440094e+09       8                      1.036591   
3  1.440094e+09       8                      1.076537   
4  1.440094e+09       8                      1.152467   

   raw_acc:magnitude_stats:std  raw_acc:magnitude_stats:moment3  \
0                     0.126916                         0.209004   
1                     0.211577                         0.189190   
2                     0.285806                        -0.132830   
3                     0.265645                         0.142064   
4                     0.350221                         0.292778   

   raw_acc:magnitude_stats:moment4  raw_acc:magnitude_stats:percentile25  \
0                         0.333994                              0.956588   
1                         0.312424                              0.875169   
2                         0.343141                              0.788695   
3                         0.322576                              0.854440   
4                         0.439607                              0.857681   

   raw_acc:magnitude_stats:percentile50  raw_acc:magnitude_stats:percentile75  \
0                              0.992468                              1.033735   
1                              1.003510                              1.153094   
2                              1.072480                              1.272836   
3                              1.071343                              1.288627   
4                              1.070274                              1.418371   

   raw_acc:magnitude_stats:value_entropy  ...  day_of_month  cl_latitude  \
0                               1.399579  ...            20       32.881   
1                               2.234364  ...            20       32.881   
2                               2.705906  ...            20       32.881   
3                               2.813417  ...            20       32.880   
4                               2.739190  ...            20       32.880   

   cl_longitude  minute_of_hour  minute_of_day  time_diff_in_minute  \
0      -117.234               7           1087             0.000000   
1      -117.234               8           1088             1.000000   
2      -117.235               9           1089             1.000000   
3      -117.235              10           1090             1.016667   
4      -117.235              11           1091             0.983333   

   pleasant_score  arousal_score  dominance_score  emotion  
0            8.47           6.05             7.21      2.0  
1            8.47           6.05             7.21      2.0  
2            8.47           6.05             7.21      2.0  
3            8.47           6.05             7.21      2.0  
4            8.47           6.05             7.21      2.0  

[5 rows x 285 columns]

In [6]:
sum(sel_feat_df['time_diff_in_minute'])

135709.68333333093

In [7]:
sel_feat_df['time_diff_in_minute'].max()

117113.45

In [8]:
sel_feat_df['time_diff_in_minute'].min()

-154269.05

In [9]:
for i in range(1, sel_feat_df.shape[0]):
    #print(i)
    if sel_feat_df['person'].iloc[i]!=sel_feat_df['person'].iloc[i-1]:
        print(sel_feat_df['time_diff_in_minute'].iloc[i])
        sel_feat_df['time_diff_in_minute'].iloc[i]=0.0
        print(i)

1845.0833333333333
1318


C:\Users\dihla\Anaconda3\lib\site-packages\pandas\core\indexing.py:190: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


117113.45
7054
-154269.05
9543
108260.66666666667
15552
-71822.68333333333
18226
-9044.8
21105
21296.633333333335
27368
60640.066666666666
28532
-62633.86666666667
29994
-8831.583333333334
34104
-39633.45
37798
29307.466666666667
40948
251.8
44544
-59055.35
50228
-80579.5
53375
12815.016666666666
57527
95356.25
60162


In [10]:
sum(sel_feat_df['time_diff_in_minute'])

174693.53333333213

In [11]:
sel_feat_df['time_diff_in_minute'].max()

5809.366666666667

In [12]:
sel_feat_df['time_diff_in_minute'].min()

0.0

In [13]:
sel_feat_df.head()

timestamp  person  raw_acc:magnitude_stats:mean  \
0  1.440094e+09       8                      1.001473   
1  1.440094e+09       8                      1.020985   
2  1.440094e+09       8                      1.036591   
3  1.440094e+09       8                      1.076537   
4  1.440094e+09       8                      1.152467   

   raw_acc:magnitude_stats:std  raw_acc:magnitude_stats:moment3  \
0                     0.126916                         0.209004   
1                     0.211577                         0.189190   
2                     0.285806                        -0.132830   
3                     0.265645                         0.142064   
4                     0.350221                         0.292778   

   raw_acc:magnitude_stats:moment4  raw_acc:magnitude_stats:percentile25  \
0                         0.333994                              0.956588   
1                         0.312424                              0.875169   
2                         0.343141                              0.788695   
3                         0.322576                              0.854440   
4                         0.439607                              0.857681   

   raw_acc:magnitude_stats:percentile50  raw_acc:magnitude_stats:percentile75  \
0                              0.992468                              1.033735   
1                              1.003510                              1.153094   
2                              1.072480                              1.272836   
3                              1.071343                              1.288627   
4                              1.070274                              1.418371   

   raw_acc:magnitude_stats:value_entropy  ...  day_of_month  cl_latitude  \
0                               1.399579  ...            20       32.881   
1                               2.234364  ...            20       32.881   
2                               2.705906  ...            20       32.881   
3                               2.813417  ...            20       32.880   
4                               2.739190  ...            20       32.880   

   cl_longitude  minute_of_hour  minute_of_day  time_diff_in_minute  \
0      -117.234               7           1087             0.000000   
1      -117.234               8           1088             1.000000   
2      -117.235               9           1089             1.000000   
3      -117.235              10           1090             1.016667   
4      -117.235              11           1091             0.983333   

   pleasant_score  arousal_score  dominance_score  emotion  
0            8.47           6.05             7.21      2.0  
1            8.47           6.05             7.21      2.0  
2            8.47           6.05             7.21      2.0  
3            8.47           6.05             7.21      2.0  
4            8.47           6.05             7.21      2.0  

[5 rows x 285 columns]

In [14]:
#new_df=sel_feat_df[sel_feat_df.person!=8]
new_df=sel_feat_df

In [15]:
# vectorized haversine function to cacluate geo distance in meter
# geo_distance is the distance the person travelled between two consecutive time-stamps
def haversine_np(lat1, lon1, lat2, lon2, to_radians=True, earth_radius=6371):
    """
    slightly modified version: of http://stackoverflow.com/a/29546836/2901002

    Calculate the great circle distance between two points
    on the earth (specified in decimal degrees or in radians)

    All (lat, lon) coordinates must have numeric dtypes and be of equal length.

    """
    if to_radians:
        lat1, lon1, lat2, lon2 = np.radians([lat1, lon1, lat2, lon2])
        print(lat1, lon1, lat2, lon2)

    a = np.sin((lat2-lat1)/2.0)**2 + np.cos(lat1) * np.cos(lat2) * np.sin((lon2-lon1)/2.0)**2

    return earth_radius * 2 * np.arcsin(np.sqrt(a))*1000



new_df['p_latitude'] = new_df['latitude'].shift(1)
new_df['p_longitude'] = new_df['longitude'].shift(1)



geo_dist = new_df[['p_latitude', 'p_longitude', 'latitude','longitude']].apply(lambda x: haversine_np(x[1], x[0], x[3], x[2]), axis=1)

geo_dist[0]=0

# assigne calulated geo_distance to the dataframe
new_df.insert(loc=new_df.shape[1]-4, column='geo_dist', value=geo_dist)

nan nan -2.0461213722248424 0.573878238143044
-2.0461213722248424 0.573878238143044 -2.0461221576230058 0.5738780287035338
-2.0461221576230058 0.5738780287035338 -2.0461323677991294 0.5738814495488677
-2.0461323677991294 0.5738814495488677 -2.046133659342776 0.5738678708872872
-2.046133659342776 0.5738678708872872 -2.0461269049185713 0.5738557059424009
-2.0461269049185713 0.5738557059424009 -2.0461130993641876 0.5738562819010539
-2.0461130993641876 0.5738562819010539 -2.0460977753733554 0.5738522850970669
-2.0460977753733554 0.5738522850970669 -2.0460847203105503 0.5738491958642908
-2.0460847203105503 0.5738491958642908 -2.0460760983840456 0.5738451990603038
-2.0460760983840456 0.5738451990603038 -2.0460765870762363 0.5738457750189568
-2.0460765870762363 0.5738457750189568 -2.046076848875624 0.5738451990603038
-2.046076848875624 0.5738451990603038 -2.046077128128304 0.5738459844584672
-2.046077128128304 0.5738459844584672 -2.046076185650508 0.5738452863267663
-2.046076185650508 0.57384

In [16]:
#new_df.drop(['p_latitude'], inplace=True)
#new_df.drop(['p_longitude'], inplace=True)

In [17]:
new_df['geo_dist'].max()

145941.73860086885

In [18]:
new_df['geo_dist'].min()

0.0

In [19]:
for i in range(1, new_df.shape[0]):
    #print(i)
    if new_df['person'].iloc[i]!=new_df['person'].iloc[i-1]:
        print(new_df['geo_dist'].iloc[i])
        new_df['geo_dist'].iloc[i]=0.0
        print(i)

158.65381662079542
1318
287.65321326751416
7054
nan
9543
613.3515469327364
15552
406.8242057478292
18226
28965.53204005393
21105
nan
27368
nan
28532
1836.2448548970547
29994
625.1888530081648
34104
1927.1388015491866
37798
9.179883259385015
40948
998.4832745913578
44544
467.3389851087339
50228
590.2882631053346
53375
nan
57527
nan
60162


In [20]:
new_df['geo_dist'].max()

145941.73860086885

In [21]:
new_df.head()

timestamp  person  raw_acc:magnitude_stats:mean  \
0  1.440094e+09       8                      1.001473   
1  1.440094e+09       8                      1.020985   
2  1.440094e+09       8                      1.036591   
3  1.440094e+09       8                      1.076537   
4  1.440094e+09       8                      1.152467   

   raw_acc:magnitude_stats:std  raw_acc:magnitude_stats:moment3  \
0                     0.126916                         0.209004   
1                     0.211577                         0.189190   
2                     0.285806                        -0.132830   
3                     0.265645                         0.142064   
4                     0.350221                         0.292778   

   raw_acc:magnitude_stats:moment4  raw_acc:magnitude_stats:percentile25  \
0                         0.333994                              0.956588   
1                         0.312424                              0.875169   
2                         0.343141                              0.788695   
3                         0.322576                              0.854440   
4                         0.439607                              0.857681   

   raw_acc:magnitude_stats:percentile50  raw_acc:magnitude_stats:percentile75  \
0                              0.992468                              1.033735   
1                              1.003510                              1.153094   
2                              1.072480                              1.272836   
3                              1.071343                              1.288627   
4                              1.070274                              1.418371   

   raw_acc:magnitude_stats:value_entropy  ...  minute_of_hour  minute_of_day  \
0                               1.399579  ...               7           1087   
1                               2.234364  ...               8           1088   
2                               2.705906  ...               9           1089   
3                               2.813417  ...              10           1090   
4                               2.739190  ...              11           1091   

   time_diff_in_minute  pleasant_score  arousal_score   geo_dist  \
0             0.000000            8.47           6.05   0.000000   
1             1.000000            8.47           6.05   5.040893   
2             1.000000            8.47           6.05  65.809210   
3             1.016667            8.47           6.05  40.436150   
4             0.983333            8.47           6.05  55.765343   

   dominance_score  emotion  p_latitude  p_longitude  
0             7.21      2.0         NaN          NaN  
1             7.21      2.0   32.880801  -117.234119  
2             7.21      2.0   32.880789  -117.234164  
3             7.21      2.0   32.880985  -117.234749  
4             7.21      2.0   32.880207  -117.234823  

[5 rows x 288 columns]

In [22]:
new_df.shape

(63648, 288)

In [23]:
#hours_in_day = 24
#days_in_week = 7


#sin_hour = np.sin(2*np.pi*new_df.hour_of_timestamp/hours_in_day)
#cos_hour = np.cos(2*np.pi*new_df.hour_of_timestamp/hours_in_day)
#new_df.insert(loc=new_df.shape[1]-4, column='sin_hour', value=sin_hour)
#new_df.insert(loc=new_df.shape[1]-4, column='cos_hour', value=cos_hour)

#sin_day = np.sin(2*np.pi*new_df.day_of_timestamp/days_in_week)
#cos_day = np.cos(2*np.pi*new_df.day_of_timestamp/days_in_week)

#new_df.insert(loc=new_df.shape[1]-4, column='sin_day', value=sin_day)
#new_df.insert(loc=new_df.shape[1]-4, column='cos_day', value=cos_day)

In [24]:
new_df.dropna(axis=1,how='all', inplace=True)

In [25]:
new_df.shape

(63648, 288)

In [26]:
import pandas_profiling as pp
#pp.ProfileReport(df)
profile=pp.ProfileReport(new_df)
rejected_variables=profile.get_rejected_variables(threshold=0.9)
#profile.to_file(r'C:\Users\dihla\Desktop\ExtraSensory_data\emotional_rating_data_18\emotion_profile_pAll_3Emotions.html')

In [27]:
#new_df.drop(['latitude', 'longitude','minute_of_day'], axis=1, inplace=True)
new_df.drop(['latitude', 'longitude'], axis=1, inplace=True)

In [28]:
new_df.shape

(63648, 286)

In [29]:
new_df['label:IN_A_CAR'].sum()

1603.0

In [30]:
mask_1=new_df['label:DRIVE_-_I_M_THE_DRIVER']==1
new_df['label:IN_A_CAR'].loc[mask_1]=1
new_df['label:IN_A_CAR'].sum()
# 'label:ON_A_BUS', ,
# 'label:DRIVE_-_I_M_A_PASSENGER',
# 'label:IN_A_CAR',

C:\Users\dihla\Anaconda3\lib\site-packages\pandas\core\indexing.py:190: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


2719.0

In [31]:
mask_2=new_df['label:DRIVE_-_I_M_A_PASSENGER']==1
new_df['label:IN_A_CAR'].loc[mask_2]=1
new_df['label:IN_A_CAR'].sum()

3392.0

In [32]:
new_df['label:IN_A_CAR'].loc[mask_2].shape

(1149,)

In [33]:
print(new_df['label:OR_indoors'].sum())
print(new_df['label:OR_outside'].sum())

38738.0
3672.0


In [34]:
mask_indoor=new_df['label:DOING_LAUNDRY']==1 
new_df['label:OR_indoors'].loc[mask_indoor]=1
new_df['label:OR_outside'].loc[mask_indoor]=0

print(new_df['label:OR_indoors'].sum())
print(new_df['label:OR_outside'].sum())

38738.0
3672.0


In [35]:
mask_outside=(new_df['label:IN_A_CAR']==1) |  (new_df['label:ON_A_BUS']==1) |   (new_df['label:LOC_beach']==1)
new_df['label:OR_indoors'].loc[mask_outside]=0
new_df['label:OR_outside'].loc[mask_outside]=1

print(new_df['label:OR_indoors'].sum())
print(new_df['label:OR_outside'].sum())


38614.0
6778.0


In [36]:
rejected_variables


['audio_naive:mfcc10:std',
 'audio_naive:mfcc11:std',
 'audio_naive:mfcc12:std',
 'audio_naive:mfcc3:std',
 'audio_naive:mfcc4:std',
 'audio_naive:mfcc5:std',
 'audio_naive:mfcc6:std',
 'audio_naive:mfcc7:std',
 'audio_naive:mfcc8:std',
 'audio_naive:mfcc9:std',
 'cl_latitude',
 'cl_longitude',
 'discrete:app_state:missing',
 'discrete:ringer_mode:missing',
 'label:AT_THE_GYM',
 'label:OR_exercise',
 'label:STAIRS_-_GOING_DOWN',
 'location:diameter',
 'location:max_altitude',
 'minute_of_day',
 'p_latitude',
 'p_longitude',
 'proc_gyro:3d:std_x',
 'proc_gyro:3d:std_y',
 'proc_gyro:magnitude_stats:moment3',
 'proc_gyro:magnitude_stats:moment4',
 'proc_gyro:magnitude_stats:percentile25',
 'proc_gyro:magnitude_stats:percentile50',
 'proc_gyro:magnitude_stats:percentile75',
 'raw_acc:magnitude_spectrum:log_energy_band2',
 'raw_acc:magnitude_spectrum:log_energy_band3',
 'raw_acc:magnitude_spectrum:log_energy_band4',
 'raw_acc:magnitude_spectrum:spectral_entropy',
 'raw_acc:magnitude_stats:m

In [38]:
# drop temporary variables and LAB_work variable
#LAB_work variable has only 1 value in the entire file
new_df.drop(['label:LAB_WORK', 'p_latitude', 'p_longitude'], axis=1, inplace=True)

In [39]:
#save the dataframe
new_df.to_csv(r'C:\Users\dihla\Desktop\ExtraSensory_data\emotional_rating_data_18\raw_Emotion_pALL_ALLFeat_updated2.csv', index=False)
